In [2]:
import pandas as pd
import scipy.io as sio
from scipy import signal, stats
import numpy as np
import datetime
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import re

midDF = pd.read_csv('midestuary_2013_2014_processed.csv', parse_dates = ['DN'], header = 0).sort_values(['DN'], ascending = [True])
riverDF = pd.read_csv('river_temperature_interpol13_14.csv', parse_dates = ['DN'], header = 0).sort_values(['DN'], ascending = [True])
oceanDF = pd.read_csv('ocean_temperature_interpol13_14.csv', parse_dates = ['DN'], header = 0).sort_values(['DN'], ascending = [True])
airTempDF = pd.read_csv('weather_2013_2014_processed.csv', parse_dates = ['DN'], header = 0).sort_values(['DN'], ascending = [True])
#riverDF = pd.read_csv('river_temperature13_14.csv', parse_dates = ['DN', 'dayDN'], header = 0).sort_values(['dayDN'], ascending = [True])
#oceanDF = pd.read_csv('ocean_temperature13_14.csv', parse_dates = ['DN', 'dayDN'], header = 0).sort_values(['dayDN'], ascending = [True])
midDF['dayDN'] = midDF['DN'].dt.floor('D')
riverDF['dayDN'] = riverDF['DN'].dt.floor('D')
oceanDF['dayDN'] = oceanDF['DN'].dt.floor('D')
# SURFACE TEMPERATURE MODEL
airTempDF = pd.merge_asof(midDF, airTempDF, on = 'DN')[["DN", "AirTemp"]]
modelSurfaceDF = pd.DataFrame({"DN" : midDF['DN']})

for index, row in midDF.iterrows():
    if oceanDF.loc[oceanDF["dayDN"] == row["dayDN"]]["OceanTemp"].shape[0] > 0 and riverDF.loc[riverDF["dayDN"] == row["dayDN"]]["EstimatedTemp"].shape[0] > 0: 
        tempDeriv = (oceanDF.loc[oceanDF["dayDN"] == row["dayDN"]]["OceanTemp"].iloc[0] - riverDF.loc[riverDF["dayDN"] == row["dayDN"]]["EstimatedTemp"].iloc[0]) / 32.0
        tempIntercept = riverDF.loc[riverDF["dayDN"] == row["dayDN"]]["EstimatedTemp"].iloc[0]
        surfaceModel = tempDeriv * row["SurfaceSalCorrected"] + tempIntercept
        tempDiff = row["SurfaceTemp"] - surfaceModel
        modelSurfaceDF.loc[index, ["ModelTemp"]] = surfaceModel
        modelSurfaceDF.loc[index, ["TempDiff"]] = tempDiff
        modelSurfaceDF.loc[index, ["OriginalTemp"]] = row["SurfaceTemp"]
    else:
        #print(row['DN'], "Ocean :", oceanDF.loc[oceanDF["DN"] == row["DN"]], "River : ", riverDF.loc[riverDF["DN"] == row["DN"]])

        modelSurfaceDF.loc[index, ["ModelTemp"]] = np.nan
        modelSurfaceDF.loc[index, ["TempDiff"]] = np.nan
        modelSurfaceDF.loc[index, ["OriginalTemp"]] = row["SurfaceTemp"]
modelSurfaceDF.to_csv("surface_temperature_model_mid13-14.csv", index = False)
tempFigLabels = ['Predicted', 'Midestuary', 'Difference', 'AirTemp']
tempfig = px.line(x = modelSurfaceDF['DN'], y = [modelSurfaceDF['ModelTemp'], modelSurfaceDF['OriginalTemp'], modelSurfaceDF['TempDiff'], airTempDF["AirTemp"]], color_discrete_sequence= ["blue", "black", "red", "purple"], title = "Temperature")
for idx in range(len(tempFigLabels)):
    tempfig.data[idx].name = tempFigLabels[idx]
    tempfig.data[idx].hovertemplate = 'variable=' + tempFigLabels[idx] + '<br>x=%{x}<br>value=%{y}<extra></extra>'
    tempfig.data[idx].legendgroup = tempFigLabels[idx]

tempfig.update_layout(title=dict(text= "Temperature for 2013-2014", font=dict(size=25)))
tempfig.update_xaxes(tickangle=30)
tempfig.update_xaxes(rangeslider_visible=True)
tempfig.update_xaxes(range = [pd.Timestamp('2013-10-22'),pd.Timestamp('2014-03-17')])

tempfig.update_layout(xaxis_title="Date", yaxis_title="Temperature (°C)", legend_title="Locations")
tempfig.show()